In [1]:
from shapely.geometry import Point
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
import pyproj
import requests
%matplotlib inline

## Jobs Density

In [2]:
# bring in jobs density: you'll need a folder called "jobs_urban_core", with the shapefile files in it
jobs_density = gpd.read_file('../data/jobs_urban_core/jobs_urban_core.shp')

In [3]:
#create new id to match for choropleth
jobs_density['id'] = jobs_density.index.astype(str)

In [4]:
#put this id first
jobs_density = jobs_density[['id', 'GEOID', 'jobs', 'geometry']]

In [5]:
#check the input data
jobs_density.head()

id         GEOID   jobs                                           geometry
0  0  470370165002  27576  POLYGON ((-86.80681 36.14488, -86.80643 36.145...
1  1  470370195003  21720  POLYGON ((-86.79050 36.16217, -86.79015 36.162...
2  2  470370195001  19786  POLYGON ((-86.78614 36.15716, -86.78606 36.157...
3  3  470370195004  17968  POLYGON ((-86.78435 36.16964, -86.78406 36.169...
4  4  470370195002  16760  POLYGON ((-86.80272 36.15248, -86.80083 36.153...

In [6]:
#check that crs is ESPG 4326 and it's a GDF:
print(jobs_density.crs)
print(type(jobs_density))

epsg:4326
<class 'geopandas.geodataframe.GeoDataFrame'>


## Bus Stops

In [7]:
# bring in bus stops: you'll need a folder called "bus_stops_bg", with the shapefile files in it
# these have associated Census Block Groups... don't use them but they're there
bus_stops = gpd.read_file('../data/bus_stops_bg/bus_stops.shp')

In [8]:
#check that crs is ESPG 4326 and it's a GDF:
print(bus_stops.crs)
print(type(bus_stops))

epsg:4269
<class 'geopandas.geodataframe.GeoDataFrame'>


In [9]:
#check the input data:
bus_stops.head(3)

Stop ID Stop Abbre                            Stop Name Route Numb  \
0     4603     LENNOX       LENNOX VILLAGE DR 1ST BUS STOP         33   
1     4647   BRENOLNN  BRENTWOOD HIGHLANDS DR & NOLENSVILL         33   
2     4604       WMOH   WAL MART - O.H. & NOLENSVILLE PIKE         33   

                     Route Name   lat_left  long_left               location  \
0  HICKORY HOLLOW-LENOX EXPRESS  36.025437 -86.712243  36.025437, -86.712243   
1  HICKORY HOLLOW-LENOX EXPRESS  36.035421 -86.713241  36.035421, -86.713241   
2  HICKORY HOLLOW-LENOX EXPRESS  36.040995 -86.710992  36.040995, -86.710992   

   index_righ STATEFP COUNTYFP TRACTCE BLKGRPCE         GEOID    ALAND  \
0          72      47      037  019120        1  470370191201   568126   
1         158      47      037  019112        2  470370191122  3503169   
2         158      47      037  019112        2  470370191122  3503169   

   AWATER    lat_right    long_right                    geometry  
0       0  +36.0207520  -086.7076439  POINT (-86.71224 36.02544)  
1       0  +36.0341746  -086.6985801  POINT (-86.71324 36.03542)  
2       0  +36.0341746  -086.6985801  POINT (-86.71099 36.04100)

## Promise Zones

In [10]:
#read 'em in, file folder called "promise_zones"
promise_zones = gpd.read_file('../data/promise_zones/promise_zones.shp')

In [11]:
#check stuff:
print(promise_zones.crs)
print(type(promise_zones))

epsg:4326
<class 'geopandas.geodataframe.GeoDataFrame'>


In [12]:
promise_zones.head()

OBJECTID  ZONE_ID    SHAPE_STAr     SHAPE_STLe  \
0         1        1  1.053728e+08   49364.601403   
1         2        2  7.670585e+07   45226.018917   
2         3        3  2.985488e+08   75207.067487   
3         4        4  2.713638e+08   74348.596054   
4         5        5  3.928178e+08  106661.712102   

                                            geometry  
0  POLYGON ((-86.76297 36.19364, -86.76297 36.193...  
1  POLYGON ((-86.77838 36.14889, -86.77823 36.148...  
2  POLYGON ((-86.70771 36.16723, -86.70758 36.166...  
3  POLYGON ((-86.74735 36.13036, -86.74728 36.130...  
4  POLYGON ((-86.78490 36.23358, -86.78452 36.232...

In [13]:
#promise_zones['value']= 1

## Then Add Your Scooter Data

## Map it all Together

In [14]:
#basemap (used state cap. for the lat/long)
base = folium.Map(location = [36.165096, -86.783637], zoom_start = 11, control_scale = True)

#create a choropleth map of jobs density:
folium.Choropleth(
    geo_data = jobs_density,
    name = 'Jobs Density in the Urban Core',
    data = jobs_density,
    columns = ['id','jobs'],
    key_on = 'feature.id',
    fill_color = 'BuPu',
    fill_opacity = 0.8,
    line_opacity = 0.2,
    line_color = 'black',
    line_weight = 1,
    highlight = True,
    smooth_factor = 1.0,
    legend_name = 'Jobs Per Census Block Group in Downtown Core').add_to(base)

#create a tooltip for the urban core census blocks of job count
folium.features.GeoJson(jobs_density,  
                        name='Job Counts',
                        style_function=lambda x: {'color':'transparent','fillColor':'transparent','weight':0},
                        tooltip=folium.features.GeoJsonTooltip(fields=['jobs'],
                                                                aliases = ['Jobs'],
                                                                labels=True,
                                                                sticky=False)).add_to(base)

#create cluster with bus stops
marker_cluster = MarkerCluster(name = 'Bus Stops').add_to(base)

for row_index, row_values in bus_stops.iterrows():
    loc = [row_values['lat_left'], row_values['long_left']]
    pop = str(row_values['Route Name'])
    icon=folium.Icon(color="blue",icon="bus", prefix='fa')
    
    marker = folium.Marker(
        location = loc, 
        popup = pop, icon = icon) 
    
    marker.add_to(marker_cluster)

#add promise zones polygons
folium.GeoJson(promise_zones, name = 'Promise Zones').add_to(base)

#enable layer control
folium.LayerControl().add_to(base)

#show map
base

In [15]:
#save to html
base.save('../maps/basemap.html')